In [ ]:
from xgboost import XGBClassifier
import pandas as pd
import numpy as np
import pickle
from sklearn.neural_network import MLPClassifier
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score
from sklearn.ensemble import RandomForestClassifier

In [2]:
!cat models/20192009_6/train.csv | wc -l

26617


In [3]:
!ls models/20192009_6/

train-data-10_1.csv  train-data-1_3.csv   train-data-3_1.csv
train-data-10_2.csv  train-data-1_6.csv   train-data-40_4.csv
train-data-10_4.csv  train-data-1_7.csv   train-data-6_1.csv
train-data-13_1.csv  train-data-21_2.csv  train.csv
train-data-18_2.csv  train-data-30_3.csv
train-data-19_2.csv  train-data-33_5.csv


In [5]:
features = ["f" + str(i) for i in range(0,33)]
label = ["action"]

headers = features + label

df = pd.read_csv('models/20192009_6/train.csv', 
                 sep = ',', 
                 header = None,
                 names = headers)
df

f0  f1  f2  f3   f4  f5  f6   f7   f8  f9  ...  f24  f25  f26  f27  \
0      232   2   2  76  687  -2   6 -129  675  -2  ...  687   -2    6 -187   
1      232   2   2  74  685  -2   6 -127  669  -2  ...  686   -2    6 -185   
2      232   2   2  72  683  -2   6 -125  663  -2  ...  685   -2    6 -183   
3      240   2   2  78  681  -2   6 -115  657  -2  ...  684   -2    6 -173   
4      240   2   2  76  679  -2   6 -113  651  -2  ...  683   -2    6 -171   
...    ...  ..  ..  ..  ...  ..  ..  ...  ...  ..  ...  ...  ...  ...  ...   
26612  217   2   5   8  457   1   2 -124  259   1  ...   37    0    3   79   
26613  217   2   5   6  452   1   2 -125  257   1  ...   30    0    3   79   
26614  217   2   5   4  447   1   2 -126  255   1  ...   23    0    3   79   
26615  217   2   5   2  442   1   2 -127  253   1  ...   16    0    3   79   
26616  217   2   5   0  437   1   2 -128  251   1  ...    9    0    3   79   

       f28  f29  f30  f31  f32  action  
0      629   -1    3  148  643       0  
1      623   -1    3  149  640       4  
2      617   -1    3  150  637       5  
3      611   -1    3  159  634       1  
4      605   -1    3  160  631       5  
...    ...  ...  ...  ...  ...     ...  
26612  625    1    2  -71  510       3  
26613  622    1    2  -72  508       3  
26614  619    1    2  -73  506       3  
26615  616    1    2  -74  504       3  
26616  613    1    2  -75  502       3  

[26617 rows x 34 columns]

In [6]:
print("headers length: {}, df lenght: {}".format(len(headers), len(df)))

headers length: 34, df lenght: 26617


In [7]:
df["f0"].value_counts()

25     6752
136    1018
248     768
168     713
144     671
       ... 
407       1
433       1
441       1
448       1
159       1
Name: f0, Length: 161, dtype: int64

In [8]:
print("different actions count \n{}".format(df.drop_duplicates()['action'].value_counts()))

different actions count 
2    8566
3    4303
5    3685
0    3635
1    3271
4    3157
Name: action, dtype: int64


In [9]:
print("no of states without duplicates: {}".format(len(df.drop_duplicates())))

no of states without duplicates: 26617


In [10]:
y_train_all = df["action"]
X_train_all = df.drop(columns="action")

In [11]:
print("no of states without duplicates and action column: {}".format(len(X_train_all.drop_duplicates())))

no of states without duplicates and action column: 26617


In [12]:
import pandas_profiling
pandas_profiling.ProfileReport(df)

In [13]:
# X_train_all[["f0", "f1"]]

In [14]:
def evaluate_model(xtrain, ytrain, xtest, ytest, model):
    y_pred_test = model.predict(xtest)
    y_pred_train = model.predict(xtrain)
    test_accuracy = accuracy_score(ytest, y_pred_test)
    train_accuracy = accuracy_score(ytrain, y_pred_train)
    print('Training accuracy: {0:.2f}, evaluation accuracy: {1:.2f}'.format(train_accuracy, test_accuracy))


Basic logisting regresion

In [15]:
X_train, X_test, y_train, y_test = train_test_split(X_train_all, y_train_all, test_size=0.2)

classifier = LogisticRegression().fit(X_train, y_train)

In [16]:
evaluate_model(X_train, y_train, X_test, y_test, classifier)

Training accuracy: 0.38, evaluation accuracy: 0.37


In [17]:
pickle.dump(classifier, open("ai_model_logit.pkl","wb"))

xgboost

In [18]:
X_train, X_test, y_train, y_test = train_test_split(X_train_all, y_train_all, 
                                                    test_size=0.2, random_state=7)

xgb_model = XGBClassifier(n_estimators=500).fit(X_train, y_train,eval_set = [[X_test, y_test]], verbose = 1)

[0]	validation_0-merror:0.610819
[1]	validation_0-merror:0.612697
[2]	validation_0-merror:0.612697
[3]	validation_0-merror:0.6142
[4]	validation_0-merror:0.610255
[5]	validation_0-merror:0.607438
[6]	validation_0-merror:0.608377
[7]	validation_0-merror:0.60556
[8]	validation_0-merror:0.606311
[9]	validation_0-merror:0.609316
[10]	validation_0-merror:0.607626
[11]	validation_0-merror:0.606687
[12]	validation_0-merror:0.60725
[13]	validation_0-merror:0.606499
[14]	validation_0-merror:0.605935
[15]	validation_0-merror:0.60556
[16]	validation_0-merror:0.60556
[17]	validation_0-merror:0.604057
[18]	validation_0-merror:0.60293
[19]	validation_0-merror:0.60293
[20]	validation_0-merror:0.603869
[21]	validation_0-merror:0.603494
[22]	validation_0-merror:0.603494
[23]	validation_0-merror:0.604433
[24]	validation_0-merror:0.605372
[25]	validation_0-merror:0.605372
[26]	validation_0-merror:0.606311
[27]	validation_0-merror:0.606311
[28]	validation_0-merror:0.604245
[29]	validation_0-merror:0.60386

[239]	validation_0-merror:0.558227
[240]	validation_0-merror:0.558227
[241]	validation_0-merror:0.558039
[242]	validation_0-merror:0.558603
[243]	validation_0-merror:0.558227
[244]	validation_0-merror:0.558415
[245]	validation_0-merror:0.558039
[246]	validation_0-merror:0.558039
[247]	validation_0-merror:0.557663
[248]	validation_0-merror:0.555973
[249]	validation_0-merror:0.556724
[250]	validation_0-merror:0.556724
[251]	validation_0-merror:0.556536
[252]	validation_0-merror:0.556349
[253]	validation_0-merror:0.556536
[254]	validation_0-merror:0.556349
[255]	validation_0-merror:0.556161
[256]	validation_0-merror:0.556161
[257]	validation_0-merror:0.555409
[258]	validation_0-merror:0.555409
[259]	validation_0-merror:0.555597
[260]	validation_0-merror:0.55447
[261]	validation_0-merror:0.554846
[262]	validation_0-merror:0.555409
[263]	validation_0-merror:0.555597
[264]	validation_0-merror:0.555409
[265]	validation_0-merror:0.556912
[266]	validation_0-merror:0.5571
[267]	validation_0-merr

[474]	validation_0-merror:0.547709
[475]	validation_0-merror:0.547896
[476]	validation_0-merror:0.547521
[477]	validation_0-merror:0.547145
[478]	validation_0-merror:0.546957
[479]	validation_0-merror:0.546769
[480]	validation_0-merror:0.546957
[481]	validation_0-merror:0.546582
[482]	validation_0-merror:0.546206
[483]	validation_0-merror:0.546582
[484]	validation_0-merror:0.54583
[485]	validation_0-merror:0.546018
[486]	validation_0-merror:0.546394
[487]	validation_0-merror:0.546769
[488]	validation_0-merror:0.546957
[489]	validation_0-merror:0.547145
[490]	validation_0-merror:0.546957
[491]	validation_0-merror:0.547145
[492]	validation_0-merror:0.546769
[493]	validation_0-merror:0.547333
[494]	validation_0-merror:0.547333
[495]	validation_0-merror:0.547521
[496]	validation_0-merror:0.546582
[497]	validation_0-merror:0.547145
[498]	validation_0-merror:0.546582
[499]	validation_0-merror:0.546206


In [19]:
evaluate_model(X_train, y_train, X_test, y_test, xgb_model)

Training accuracy: 0.62, evaluation accuracy: 0.45


In [20]:
xgb_model = XGBClassifier(n_estimators=500).fit(X_train_all, y_train_all)

In [21]:
pickle.dump(xgb_model, open("ai_model_xgb.pkl","wb"))

random forest model

In [22]:
forest_model = RandomForestClassifier(random_state=1, n_estimators=500)
forest_model.fit(X_train, y_train)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=500,
                       n_jobs=None, oob_score=False, random_state=1, verbose=0,
                       warm_start=False)

In [23]:
evaluate_model(X_train, y_train, X_test, y_test, forest_model)

Training accuracy: 1.00, evaluation accuracy: 0.44


In [24]:
# min_max_scaler = MinMaxScaler()
# np_scaled = min_max_scaler.fit_transform(df)
# df_normalized = pd.DataFrame(np_scaled)
# df_normalized.columns = feature_cols + ['Class']

In [25]:
# def make_crosses(X_train, X_validation, degree=2):
#   from sklearn.preprocessing import PolynomialFeatures
#   poly = PolynomialFeatures(degree=degree)
#   X_train_poly = poly.fit_transform(X_train)
#   X_validation_poly = poly.transform(X_validation)
#   return X_train_poly, X_validation_poly

In [26]:
mlp_model = MLPClassifier(solver='lbfgs', alpha=1e-5, 
                    hidden_layer_sizes=(24, 24), 
                          random_state=1, verbose=True, solver='adam)

mlp_model.fit(X_train_all, y_train_all)

MLPClassifier(activation='relu', alpha=1e-05, batch_size='auto', beta_1=0.9,
              beta_2=0.999, early_stopping=False, epsilon=1e-08,
              hidden_layer_sizes=(24, 24), learning_rate='constant',
              learning_rate_init=0.001, max_iter=200000, momentum=0.9,
              n_iter_no_change=10, nesterovs_momentum=True, power_t=0.5,
              random_state=1, shuffle=True, solver='lbfgs', tol=0.0001,
              validation_fraction=0.1, verbose=False, warm_start=False)

In [27]:
evaluate_model(X_train, y_train, X_test, y_test, mlp_model)

Training accuracy: 0.32, evaluation accuracy: 0.32


Save models to pkl

In [ ]:
pickle.dump(forest_model, open("ai_model_forest.pkl","wb"))

In [28]:
pickle.dump(mlp_model, open("ai_model_mlp.pkl","wb"))

In [29]:
!bash evaluate-ai.sh

evaluation of logit
evaluation logit with 10 attempts, resulted with, avg time: 5.1 and avg score: 10.8
evaluation of xgb
evaluation xgb with 10 attempts, resulted with, avg time: 8.4 and avg score: 8.1
evaluation of mlp
evaluation mlp with 10 attempts, resulted with, avg time: 3.4 and avg score: 8.5


In [ ]:
# model_p = pickle.load(open("ai_model.pkl","rb"))
game_state_4f = (np.array([8,280,630,-1,1,674,-3,7,667,-1,2,649,-3,2,662,0,3,662,-1,4,655,-1,5,608,2,7,1,8,288,630,-1,1,672,-3,7,668,-1,2,650,-3,2,661,0,3,657,-1,4,649,-1,5,602,2,7,1,8,296,629,-1,1,670,-3,7,669,-1,2,651,-3,2,660,0,3,651,-1,4,643,-1,5,596,2,7,1,8,296,628,-1,1,665,-3,7,667,-1,2,650,-3,2,658,0,3,647,-1,4,638,-1,5,589,2,7])
                 .reshape(1, -1))



game_state_1f = (np.array([25, -410, 308, 5, 1, -343, 483, 1, 2, -417, 592, 5, 2, -184, 589, 1, 2, -222, 275, 7, 2, -93, 143, 3, -2, -128, 549, 1, -3, -121, 399, 6, -3]).reshape(1, -1))

xgb_model.predict(game_state_1f)